In [1]:
import os
import uuid
from PIL import Image  # Example image processing library
import json
from DepthScape_Classes import *
import torch
from moge.model import MoGeModel
from moge.utils.vis import colorize_depth
import utils3d
#import asyncio
from concurrent.futures import ThreadPoolExecutor
import time
import numpy as np
from DepthScape_Classes.VisualCoding import VisualCoding
from DepthScape_Classes.VisualCodingBlocks import Text2Mask, Mask2PointCloud, PointCloud2Line, PointCloud2Plane, PointCloud2Cylinder, PointCloud2Sphere, FaceExtraction, SkeletonExtraction
from DepthScape_Classes.CoordinateSystems import Planar, Cylindrical, Spherical
import trimesh
import trimesh.visual
# Configure upload folder
UPLOAD_FOLDER = 'Server_Data'
os.makedirs(UPLOAD_FOLDER, exist_ok=True)
executor = ThreadPoolExecutor()
device = torch.device('cuda')
pretrained_model_name_or_path='Ruicheng/moge-vitl'
model = MoGeModel.from_pretrained(pretrained_model_name_or_path).to(device).eval()


In [2]:
from DepthScape_Classes import *
test_image_dir='example_images/player.jpg'
id=uuid.uuid4().hex
depthScape= DepthScape(id ,test_image_dir, model, device, 'example_images')
depthScape.process_image()
#depthScape.ask_GPT()

DepthScape initialized
Processing image
Focal: tensor([3.0571], device='cuda:0')
MoGe conducted. GLB saved at example_images/1619c195358a40eb8e014ea394e08997.glb
FOV x: 0.5308845639228821
FOV y: 0.358381062746048


In [3]:
test_image_dir2='example_images/face.jpg'
id=uuid.uuid4().hex
depthScape2=DepthScape(id ,test_image_dir2, model, device, 'example_images')
depthScape2.process_image()
text_prompt2="The man"
mask2=Text2Mask.Text2Mask(depthScape2,text_prompt2)
pc2=Mask2PointCloud.Mask2PointCloud(depthScape2,mask2)

DepthScape initialized
Processing image
Focal: tensor([3.6863], device='cuda:0')


c:\Users\xiasu\Desktop\Xia\DepthScapeBackend\DepthScape_Classes\Geometry\PointCloud.py:10: RuntimeWarning: invalid value encountered in subtract
  distances = np.linalg.norm(self.points - self.center, axis=1)


MoGe conducted. GLB saved at example_images/13d4ec4033ff4143a4a7de726e635c02.glb
FOV x: 0.4339130222797394
FOV y: 0.3124227821826935
Text2Mask:The man


c:\Users\xiasu\Desktop\Xia\DepthScapeBackend\DepthScape_Classes\DepthScape.py:148: RuntimeWarning: invalid value encountered in scalar divide
  fov_y = 2 * np.arctan(np.abs(y) / z)
c:\Users\xiasu\Desktop\Xia\DepthScapeBackend\DepthScape_Classes\DepthScape.py:149: RuntimeWarning: invalid value encountered in scalar divide
  fov_x = 2 * np.arctan(np.abs(x) / z)


Mask2PointCloud for mask from text The man


In [4]:
text_prompt="The player"
mask=Text2Mask.Text2Mask(depthScape,text_prompt)
pc=Mask2PointCloud.Mask2PointCloud(depthScape,mask)


Text2Mask:The player
Mask2PointCloud for mask from text The player


In [11]:
text_prompt_face="The human face"
mask_face=Text2Mask.Text2Mask(depthScape,text_prompt_face)


Text2Mask:The human face
Error occured when parsing mask: 500, <!doctype html>
<html lang=en>
  <head>
    <title>TypeError: float() argument must be a string or a real number, not &#39;list&#39;
 // Werkzeug Debugger</title>
    <link rel="stylesheet" href="?__debugger__=yes&amp;cmd=resource&amp;f=style.css">
    <link rel="shortcut icon"
        href="?__debugger__=yes&amp;cmd=resource&amp;f=console.png">
    <script src="?__debugger__=yes&amp;cmd=resource&amp;f=debugger.js"></script>
    <script>
      var CONSOLE_MODE = false,
          EVALEX = true,
          EVALEX_TRUSTED = false,
          SECRET = "ii0oWimawHcd6uGgmn6D";
    </script>
  </head>
  <body style="background-color: #fff">
    <div class="debugger">
<h1>TypeError</h1>
<div class="detail">
  <p class="errormsg">TypeError: float() argument must be a string or a real number, not &#39;list&#39;
</p>
</div>
<h2 class="traceback">Traceback <em>(most recent call last)</em></h2>
<div class="traceback">
  <h3></h3>
  <ul><l

In [5]:
skeleton=SkeletonExtraction.SkeletonExtraction(depthScape,mask)
skeleton2=SkeletonExtraction.SkeletonExtraction(depthScape2,mask2)
face=FaceExtraction.FaceExtraction(depthScape,mask)
face2=FaceExtraction.FaceExtraction(depthScape2,mask2)


Masked skeleton image saved at example_images/player_masked_skeleton.jpg
Masked skeleton image saved at example_images/face_masked_skeleton.jpg
Masked face image saved at example_images/player_masked_face.jpg
Masked face image saved at example_images/face_masked_face.jpg


In [6]:
cranial1=skeleton.get_cranial()
anterior1=skeleton.get_anterior()
cranial2=skeleton2.get_cranial()
anterior2=skeleton2.get_anterior()
median1=skeleton.get_median()
median2=skeleton2.get_median()
frontal1=skeleton.get_frontal()
frontal2=skeleton2.get_frontal()
cranial_face=face.get_cranial()
anterior_face=face.get_anterior()
median_face=face.get_median()
frontal_face=face.get_frontal()
cranial_face2=face2.get_cranial()
anterior_face2=face2.get_anterior()
median_face2=face2.get_median()
frontal_face2=face2.get_frontal()






In [7]:
# Print out all landmarks with their meanings
landmark_meanings = {
    0: "nose",
    1: "left eye (inner)", 
    2: "left eye",
    3: "left eye (outer)",
    4: "right eye (inner)",
    5: "right eye", 
    6: "right eye (outer)",
    7: "left ear",
    8: "right ear",
    9: "mouth (left)",
    10: "mouth (right)",
    11: "left shoulder",
    12: "right shoulder", 
    13: "left elbow",
    14: "right elbow",
    15: "left wrist",
    16: "right wrist",
    17: "left pinky",
    18: "right pinky",
    19: "left index",
    20: "right index",
    21: "left thumb",
    22: "right thumb",
    23: "left hip",
    24: "right hip",
    25: "left knee",
    26: "right knee",
    27: "left ankle",
    28: "right ankle",
    29: "left heel",
    30: "right heel",
    31: "left foot index",
    32: "right foot index"
}

for i, landmark in enumerate(skeleton2.results.pose_landmarks.landmark):
    print(f"Landmark {i} ({landmark_meanings[i]})")
    print(f"  x: {landmark.x:.3f}")
    print(f"  y: {landmark.y:.3f}") 
    print(f"  z: {landmark.z:.3f}")
    print(f"  visibility: {landmark.visibility:.3f}")
    print()


Landmark 0 (nose)
  x: 0.558
  y: 0.550
  z: -1.664
  visibility: 0.998

Landmark 1 (left eye (inner))
  x: 0.565
  y: 0.427
  z: -1.573
  visibility: 0.997

Landmark 2 (left eye)
  x: 0.584
  y: 0.419
  z: -1.575
  visibility: 0.997

Landmark 3 (left eye (outer))
  x: 0.596
  y: 0.412
  z: -1.575
  visibility: 0.997

Landmark 4 (right eye (inner))
  x: 0.506
  y: 0.437
  z: -1.601
  visibility: 0.998

Landmark 5 (right eye)
  x: 0.471
  y: 0.436
  z: -1.603
  visibility: 0.998

Landmark 6 (right eye (outer))
  x: 0.438
  y: 0.436
  z: -1.604
  visibility: 0.999

Landmark 7 (left ear)
  x: 0.574
  y: 0.445
  z: -0.942
  visibility: 0.998

Landmark 8 (right ear)
  x: 0.357
  y: 0.468
  z: -1.060
  visibility: 0.997

Landmark 9 (mouth (left))
  x: 0.591
  y: 0.636
  z: -1.398
  visibility: 0.997

Landmark 10 (mouth (right))
  x: 0.513
  y: 0.643
  z: -1.444
  visibility: 0.997

Landmark 11 (left shoulder)
  x: 0.804
  y: 0.911
  z: -0.642
  visibility: 0.999

Landmark 12 (right shoulder)

In [8]:
skeleton.positions_3d

{0: array([-0.03710203, -0.1644068 ,  1.3506825 ], dtype=float32),
 1: array([-0.0399743 , -0.18005651,  1.3557465 ], dtype=float32),
 2: array([-0.03745986, -0.181115  ,  1.3637164 ], dtype=float32),
 3: array([-0.03502366, -0.18274735,  1.3760078 ], dtype=float32),
 4: array([-0.05061514, -0.1783421 ,  1.3479542 ], dtype=float32),
 5: array([-0.05596436, -0.17739032,  1.3458872 ], dtype=float32),
 6: array([-0.06327165, -0.17560436,  1.342606  ], dtype=float32),
 7: array([-0.04705625, -0.16825165,  1.3433328 ], dtype=float32),
 9: array([-0.03268191, -0.14689994,  1.3651311 ], dtype=float32),
 10: array([-0.04916367, -0.14410047,  1.345418  ], dtype=float32),
 11: array([ 0.0104973 , -0.06399973,  1.3436829 ], dtype=float32),
 12: array([-0.15767255, -0.05874079,  1.3630883 ], dtype=float32),
 13: array([0.11398327, 0.02656252, 1.3342043 ], dtype=float32),
 15: array([ 0.1159384 , -0.06267814,  1.288665  ], dtype=float32),
 17: array([ 0.11494487, -0.083567  ,  1.2705026 ], dtype=fl

In [9]:
# Create scene
scene = trimesh.Scene()

# Add point cloud visualization with blue color
pc_tri = trimesh.points.PointCloud(pc.get_downsampled_points(10000), colors=[0, 0, 255, 255])
scene.add_geometry(pc_tri)

# Add skeleton positions as spheres - red for body joints, blue for face
for idx, pos in skeleton.positions_3d.items():
    # Skip facial points from skeleton (indices 0-10)
    if idx <= 10:
        continue
        
    # Create larger sphere for body joints
    sphere = trimesh.creation.icosphere(radius=0.02)  # Bigger radius for body joints
    sphere.visual.face_colors = [255, 0, 0, 255]  # Red color
    sphere.apply_translation(pos)
    scene.add_geometry(sphere)

# Add facial points from face object with smaller blue spheres
for idx, pos in face.positions_3d.items():
    sphere = trimesh.creation.icosphere(radius=0.01)  # Smaller radius for face points
    sphere.visual.face_colors = [0, 0, 255, 255]  # Blue color
    sphere.apply_translation(pos) 
    scene.add_geometry(sphere)
# Get cranial and anterior vectors
cranial_vector = skeleton.get_cranial()
anterior_vector = skeleton.get_anterior()

if cranial_vector is not None and anterior_vector is not None:
    # Get left shoulder position as starting point
    left_shoulder_pos = skeleton.positions_3d.get(11)  # Left shoulder
    
    if left_shoulder_pos is not None:
        # Scale vectors for visualization (make them longer)
        scale = 0.2
        cranial_end = [
            left_shoulder_pos[0] + cranial_vector[0] * scale,
            left_shoulder_pos[1] + cranial_vector[1] * scale, 
            left_shoulder_pos[2] + cranial_vector[2] * scale
        ]
        anterior_end = [
            left_shoulder_pos[0] + anterior_vector[0] * scale,
            left_shoulder_pos[1] + anterior_vector[1] * scale,
            left_shoulder_pos[2] + anterior_vector[2] * scale
        ]
        
        # Create cylinders for vectors
        # Cranial vector - green
        cranial_cylinder = trimesh.creation.cylinder(
            radius=0.005,
            segment=np.array([left_shoulder_pos, cranial_end])
        )
        cranial_cylinder.visual.face_colors = [0, 255, 0, 255]
        
        # Anterior vector - yellow
        anterior_cylinder = trimesh.creation.cylinder(
            radius=0.005,
            segment=np.array([left_shoulder_pos, anterior_end])
        )
        anterior_cylinder.visual.face_colors = [255, 255, 0, 255]
        
        scene.add_geometry(cranial_cylinder)
        scene.add_geometry(anterior_cylinder)

# Get frontal and median planes
frontal_plane = skeleton.get_frontal()
median_plane = skeleton.get_median()

if frontal_plane is not None:
    # Create vertices for frontal plane boundary
    frontal_boundary = frontal_plane.get_boundary_with_span()
    
    # Create mesh for frontal plane
    frontal_mesh = trimesh.Trimesh(
        vertices=frontal_boundary,
        faces=[[0,1,2], [2,3,0], [3,0,1], [1,2,3], [2,1,0], [0,3,2], [1,0,3], [3,2,1]],  # Add back faces
        process=False
    )
    frontal_mesh.visual.face_colors = [0, 255, 255, 100]  # Cyan with transparency
    scene.add_geometry(frontal_mesh)

if median_plane is not None:
    # Create vertices for median plane boundary  
    median_boundary = median_plane.get_boundary_with_span()
    
    # Create mesh for median plane
    median_mesh = trimesh.Trimesh(
        vertices=median_boundary,
        faces=[[0,1,2], [2,3,0], [3,0,1], [1,2,3], [2,1,0], [0,3,2], [1,0,3], [3,2,1]],  # Add back faces
        process=False
    )
    median_mesh.visual.face_colors = [255, 0, 255, 100]  # Magenta with transparency
    scene.add_geometry(median_mesh)

# Get facial frontal and median planes
face_frontal_plane = face.get_frontal()
face_median_plane = face.get_median()

if face_frontal_plane is not None:
    # Create vertices for facial frontal plane boundary
    face_frontal_boundary = face_frontal_plane.get_boundary_with_span()
    
    # Create mesh for facial frontal plane
    face_frontal_mesh = trimesh.Trimesh(
        vertices=face_frontal_boundary,
        faces=[[0,1,2], [2,3,0], [3,0,1], [1,2,3], [2,1,0], [0,3,2], [1,0,3], [3,2,1]],  # Add back faces
        process=False
    )
    face_frontal_mesh.visual.face_colors = [0, 128, 255, 100]  # Light blue with transparency
    scene.add_geometry(face_frontal_mesh)

if face_median_plane is not None:
    # Create vertices for facial median plane boundary  
    face_median_boundary = face_median_plane.get_boundary_with_span()
    
    # Create mesh for facial median plane
    face_median_mesh = trimesh.Trimesh(
        vertices=face_median_boundary,
        faces=[[0,1,2], [2,3,0], [3,0,1], [1,2,3], [2,1,0], [0,3,2], [1,0,3], [3,2,1]],  # Add back faces
        process=False
    )
    face_median_mesh.visual.face_colors = [255, 128, 255, 100]  # Light magenta with transparency
    scene.add_geometry(face_median_mesh)

# Add facial cranial and anterior vectors from nose
face_cranial = face.get_cranial()
face_anterior = face.get_anterior()

if face_cranial is not None and face_anterior is not None:
    # Get nose position as origin point
    nose_pos = face.positions_3d.get(0)
    
    # Scale factor for vector visualization
    scale = 0.2
    
    # Create and add cranial vector visualization
    face_cranial_end = [
        nose_pos[0] + face_cranial[0] * scale,
        nose_pos[1] + face_cranial[1] * scale, 
        nose_pos[2] + face_cranial[2] * scale
    ]
    face_cranial_line = trimesh.creation.cylinder(
        radius=0.005,
        segment=np.array([nose_pos, face_cranial_end])
    )
    face_cranial_line.visual.face_colors = [0, 255, 0, 255]  # Green color
    scene.add_geometry(face_cranial_line)
    
    # Create and add anterior vector visualization  
    face_anterior_end = [
        nose_pos[0] + face_anterior[0] * scale,
        nose_pos[1] + face_anterior[1] * scale,
        nose_pos[2] + face_anterior[2] * scale
    ]
    face_anterior_line = trimesh.creation.cylinder(
        radius=0.005,
        segment=np.array([nose_pos, face_anterior_end])
    )
    face_anterior_line.visual.face_colors = [255, 0, 0, 255]  # Red color
    scene.add_geometry(face_anterior_line)


# Add ambient lighting from all directions
scene.ambient_light = [1000, 1000, 1000]  # Full white ambient light

# Show the scene
scene.show()


C:\Users\xiasu\AppData\Roaming\Python\Python312\site-packages\pyglet\libs\win32\__init__.py:318: UserWarning: Could not set COM MTA mode. Unexpected behavior may occur.
  warnings.warn("Could not set COM MTA mode. Unexpected behavior may occur.")


In [14]:
scene = trimesh.Scene()

# Add point cloud visualization with blue color
pc_tri = trimesh.points.PointCloud(pc2.get_downsampled_points(10000), colors=[0, 0, 255, 255])
scene.add_geometry(pc_tri)

# Add skeleton positions as spheres - red for body joints, blue for face
for idx, pos in skeleton2.positions_3d.items():
    # Skip facial points from skeleton (indices 0-10)
    if idx <= 10:
        continue
        
    # Create larger sphere for body joints
    sphere = trimesh.creation.icosphere(radius=0.02)  # Bigger radius for body joints
    sphere.visual.face_colors = [255, 0, 0, 255]  # Red color
    sphere.apply_translation(pos)
    scene.add_geometry(sphere)

# Add facial points from face object with smaller blue spheres
for idx, pos in face2.positions_3d.items():
    sphere = trimesh.creation.icosphere(radius=0.01)  # Smaller radius for face points
    sphere.visual.face_colors = [0, 0, 255, 255]  # Blue color
    sphere.apply_translation(pos) 
    scene.add_geometry(sphere)
cranial_vector = skeleton2.get_cranial()
anterior_vector = skeleton2.get_anterior()

if cranial_vector and anterior_vector:
    # Get left shoulder position as origin point
    left_shoulder_pos = skeleton2.positions_3d.get(11)
    
    # Scale factor for vector visualization
    scale = 0.2
    
    # Calculate end points
    cranial_end = [
        left_shoulder_pos[0] + cranial_vector[0] * scale,
        left_shoulder_pos[1] + cranial_vector[1] * scale,
        left_shoulder_pos[2] + cranial_vector[2] * scale
    ]
    anterior_end = [
        left_shoulder_pos[0] + anterior_vector[0] * scale,
        left_shoulder_pos[1] + anterior_vector[1] * scale,
        left_shoulder_pos[2] + anterior_vector[2] * scale
    ]
    
    # Create cylinders for vectors
    # Cranial vector - green
    cranial_cylinder = trimesh.creation.cylinder(
        radius=0.005,
        segment=np.array([left_shoulder_pos, cranial_end])
    )
    cranial_cylinder.visual.face_colors = [0, 255, 0, 255]
    
    # Anterior vector - yellow
    anterior_cylinder = trimesh.creation.cylinder(
        radius=0.005,
        segment=np.array([left_shoulder_pos, anterior_end])
    )
    anterior_cylinder.visual.face_colors = [255, 255, 0, 255]
    
    scene.add_geometry(cranial_cylinder)
    scene.add_geometry(anterior_cylinder)
# Get sagittal and frontal planes
sagittal_plane = skeleton2.get_median()
frontal_plane = skeleton2.get_frontal()

if sagittal_plane and frontal_plane:
    # Create sagittal plane visualization (blue)
    sagittal_boundary = sagittal_plane.boundary
    sagittal_mesh = trimesh.Trimesh(vertices=sagittal_boundary,
                                   faces=[[0,1,2], [2,3,0], [3,0,1], [1,2,3], [2,1,0], [0,3,2], [1,0,3], [3,2,1]],  # Add back faces
                                   face_colors=[0, 0, 255, 100])
    scene.add_geometry(sagittal_mesh)
    
    # Create frontal plane visualization (red)
    frontal_boundary = frontal_plane.boundary
    frontal_mesh = trimesh.Trimesh(vertices=frontal_boundary,
                                  faces=[[0,1,2], [2,3,0], [3,0,1], [1,2,3], [2,1,0], [0,3,2], [1,0,3], [3,2,1]],  # Add back faces
                                  face_colors=[255, 0, 0, 100])
    scene.add_geometry(frontal_mesh)
# Get facial planes
face = face2
if face:
    sagittal_plane_face = face.get_median()
    frontal_plane_face = face.get_frontal()

    if sagittal_plane_face and frontal_plane_face:
        # Create sagittal plane visualization for face (cyan)
        sagittal_boundary_face = sagittal_plane_face.boundary
        sagittal_mesh_face = trimesh.Trimesh(vertices=sagittal_boundary_face,
                                           faces=[[0,1,2], [2,3,0], [3,0,1], [1,2,3], [2,1,0], [0,3,2], [1,0,3], [3,2,1]],
                                           face_colors=[0, 255, 255, 100])
        scene.add_geometry(sagittal_mesh_face)

        # Create frontal plane visualization for face (magenta) 
        frontal_boundary_face = frontal_plane_face.boundary
        frontal_mesh_face = trimesh.Trimesh(vertices=frontal_boundary_face,
                                          faces=[[0,1,2], [2,3,0], [3,0,1], [1,2,3], [2,1,0], [0,3,2], [1,0,3], [3,2,1]],
                                          face_colors=[255, 0, 255, 100])
        scene.add_geometry(frontal_mesh_face)

# Get face anterior and cranial vectors
if face:
    nose_pos = face.positions_3d.get(0)  # Nose position
    anterior = face.get_anterior()
    cranial = face.get_cranial()
    
    if nose_pos is not None and anterior is not None and cranial is not None:
        # Scale vectors to make them visible
        scale = 0.2
        anterior_end = nose_pos + anterior * scale
        cranial_end = nose_pos + cranial * scale
        
        # Create anterior cylinder for face (orange)
        face_anterior_cylinder = trimesh.creation.cylinder(
            radius=0.005,
            segment=np.array([nose_pos, anterior_end])
        )
        face_anterior_cylinder.visual.face_colors = [255, 165, 0, 255]
        
        # Create cranial cylinder for face (purple)
        face_cranial_cylinder = trimesh.creation.cylinder(
            radius=0.005,
            segment=np.array([nose_pos, cranial_end])
        )
        face_cranial_cylinder.visual.face_colors = [128, 0, 128, 255]
        
        scene.add_geometry(face_anterior_cylinder)
        scene.add_geometry(face_cranial_cylinder)

# Add ambient lighting from all directions
scene.ambient_light = [500, 500, 500]  # Increased white ambient light intensity

# Show the scene
scene.show()

In [18]:
#cylinder=PointCloud2Cylinder.PointCloud2Cylinder(pc,None)
cylinder=PointCloud2Cylinder.PointCloud2Cylinder(pc,np.array([0,1,0]))
sphere=PointCloud2Sphere.PointCloud2Sphere(pc)


In [19]:
scene = trimesh.Scene()

# Add point cloud visualization
pc_tri = trimesh.points.PointCloud(pc.get_downsampled_points(5000), colors=np.array([0, 0, 255, 0]))
scene.add_geometry(pc_tri)

# Create cylinder visualization
# Get cylinder parameters
center = cylinder.center
axis = cylinder.axis
radius = cylinder.radius
height = cylinder.height

# Create cylinder mesh
# Create a transformation matrix to align cylinder with axis
z_axis = np.array([0, 0, 1])
rotation_axis = np.cross(z_axis, axis)
rotation_angle = np.arccos(np.dot(z_axis, axis))
if np.all(rotation_axis == 0):
    rotation_matrix = np.eye(3)
else:
    rotation_matrix = trimesh.transformations.rotation_matrix(
        angle=rotation_angle,
        direction=rotation_axis,
        point=center
    )

# Create cylinder primitive
cylinder_mesh = trimesh.creation.cylinder(
    radius=radius,
    height=height,
    sections=32,
    segment=None
)

# Create sphere mesh
sphere_mesh = trimesh.creation.icosphere(
    radius=sphere.radius,
    subdivisions=3
)

# Move sphere to center
sphere_mesh.apply_translation(sphere.center)

# Add sphere to scene with semi-transparent color
sphere_mesh.visual.face_colors = [200, 200, 200, 128]
scene.add_geometry(sphere_mesh)


# Transform cylinder to align with axis and move to center
cylinder_mesh.apply_transform(rotation_matrix)
translation = center - cylinder_mesh.center_mass
cylinder_mesh.apply_translation(translation)

# Add cylinder to scene with semi-transparent color
cylinder_mesh.visual.face_colors = [200, 200, 200, 128]
#scene.add_geometry(cylinder_mesh)
scene.show()


In [3]:
depthScape.output_coordinate_systems[0].variables
pc=depthScape.output_coordinate_systems[0].variables['MESH_0']
plane1=depthScape.output_coordinate_systems[0].plane
plane2=depthScape.output_coordinate_systems[1].plane


In [10]:
plane1

In [4]:
scene = trimesh.Scene()

# Add point cloud visualization
pc_tri = trimesh.points.PointCloud(pc.get_downsampled_points(5000), colors=np.array([0, 0, 255, 0]))
scene.add_geometry(pc_tri)

# Create plane visualization
# Get plane parameters
center = plane1.center
normal = plane1.normal
primary = plane1.primary
span = plane1.span

# Create a plane mesh using the boundary points
# plane_mesh_1 = trimesh.Trimesh(vertices=boundary, 
#                             faces=[[0,1,2], [0,2,3], [0,1,3], [1,2,3]],
#                             face_colors=[200, 200, 200, 100])
# Create corner points for plane visualization using normal, primary directions and span
corners = []
for i in [-0.5, 0.5]:
    for j in [-0.5, 0.5]:
        point = center + i * span[0] * primary[0] + j * span[1] * primary[1]
        corners.append(point)
corners = np.array(corners)

# Create plane mesh from corners
plane_mesh_1 = trimesh.Trimesh(vertices=corners,
                              faces=[[0,1,2], [0,2,3], [0,1,3], [1,2,3]],
                              face_colors=[200, 200, 200, 100])

# Create a cylinder to visualize primary[0] direction
# Create a cylinder along primary[0] direction from center
radius = 0.02  # Small radius for visualization
height = 0.5   # Length of the direction vector visualization
# Create transform matrix to orient cylinder along primary[0]
Z = primary[0] / np.linalg.norm(primary[0])  # Normalize direction
X = np.cross(Z, [0,1,0])  # Get perpendicular vector
if np.allclose(X, 0):
    X = np.cross(Z, [1,0,0])
X = X / np.linalg.norm(X)
Y = np.cross(Z, X)
transform = np.eye(4)
transform[:3,:3] = np.vstack([X, Y, Z]).T
transform[:3,3] = center

# Create cylinder mesh
cylinder1 = trimesh.creation.cylinder(radius=radius, height=height, transform=transform)
cylinder1.visual.face_colors = [255, 0, 0, 255]  # Red color for primary direction


# Create transform matrix to orient cylinder along primary[0]
Z = primary[1] / np.linalg.norm(primary[1])  # Normalize direction
X = np.cross(Z, [0,1,0])  # Get perpendicular vector
if np.allclose(X, 0):
    X = np.cross(Z, [1,0,0])
X = X / np.linalg.norm(X)
Y = np.cross(Z, X)
transform = np.eye(4)
transform[:3,:3] = np.vstack([X, Y, Z]).T
transform[:3,3] = center

# Create cylinder mesh
cylinder2 = trimesh.creation.cylinder(radius=radius, height=height, transform=transform)
cylinder2.visual.face_colors = [255, 0, 0, 255]  # Red color for primary direction

# Add cylinder to scene


center = plane2.center
normal = plane2.normal
primary = plane2.primary
span = plane2.span

# Create a plane mesh using the boundary points
# plane_mesh_2 = trimesh.Trimesh(vertices=boundary, 
#                             faces=[[0,1,2], [0,2,3], [0,1,3], [1,2,3]],
#                             face_colors=[200, 200, 200, 100])

corners = []
for i in [-0.5, 0.5]:
    for j in [-0.5, 0.5]:
        point = center + i * span[0] * primary[0] + j * span[1] * primary[1]
        corners.append(point)
corners = np.array(corners)

# Create plane mesh from corners
plane_mesh_2 = trimesh.Trimesh(vertices=corners,
                              faces=[[0,1,2], [0,2,3], [0,1,3], [1,2,3]],
                              face_colors=[200, 200, 200, 100])
                              
# Create a cylinder to visualize primary[0] direction
# Create a cylinder along primary[0] direction from center
radius = 0.02  # Small radius for visualization
height = 0.5   # Length of the direction vector visualization
# Create transform matrix to orient cylinder along primary[0]
Z = primary[0] / np.linalg.norm(primary[0])  # Normalize direction
X = np.cross(Z, [0,1,0])  # Get perpendicular vector
if np.allclose(X, 0):
    X = np.cross(Z, [1,0,0])
X = X / np.linalg.norm(X)
Y = np.cross(Z, X)
transform = np.eye(4)
transform[:3,:3] = np.vstack([X, Y, Z]).T
transform[:3,3] = center

# Create cylinder mesh
cylinder3 = trimesh.creation.cylinder(radius=radius, height=height, transform=transform)
cylinder3.visual.face_colors = [255, 0, 0, 255]  # Red color for primary direction

# Create transform matrix to orient cylinder along primary[0]
Z = primary[1] / np.linalg.norm(primary[1])  # Normalize direction
X = np.cross(Z, [0,1,0])  # Get perpendicular vector
if np.allclose(X, 0):
    X = np.cross(Z, [1,0,0])
X = X / np.linalg.norm(X)
Y = np.cross(Z, X)
transform = np.eye(4)
transform[:3,:3] = np.vstack([X, Y, Z]).T
transform[:3,3] = center

# Create cylinder mesh
cylinder4 = trimesh.creation.cylinder(radius=radius, height=height, transform=transform)
cylinder4.visual.face_colors = [255, 0, 0, 255]  # Red color for primary direction

# Add plane to scene
scene.add_geometry(plane_mesh_1)
scene.add_geometry(plane_mesh_2)
scene.add_geometry(cylinder1)
scene.add_geometry(cylinder2)
scene.add_geometry(cylinder3)
scene.add_geometry(cylinder4)

# Show the scene
scene.show()


C:\Users\xiasu\AppData\Roaming\Python\Python312\site-packages\pyglet\libs\win32\__init__.py:318: UserWarning: Could not set COM MTA mode. Unexpected behavior may occur.
  warnings.warn("Could not set COM MTA mode. Unexpected behavior may occur.")


In [20]:
mask1=Text2Mask.Text2Mask(depthScape,"the main building in the image")
#mask2=Text2Mask.Text2Mask(depthScape,"the sidewalk")
pc1= Mask2PointCloud.Mask2PointCloud(depthScape,mask1)
#pc2= Mask2PointCloud.Mask2PointCloud(depthScape,mask2)

Text2Mask:the main building in the image
Mask2PointCloud for mask from text the main building in the image


In [21]:
plane1=PointCloud2Plane.PointCloud2Plane(pc1)
scene = trimesh.Scene()

# Add point cloud visualization
pc_tri = trimesh.points.PointCloud(pc1.get_downsampled_points(5000), colors=np.array([0, 0, 255, 0]))
scene.add_geometry(pc_tri)

# Create plane visualization
# Get plane parameters
center = plane1[1].center
normal = plane1[1].normal
primary = plane1[1].primary
boundary = plane1[1].boundary

# Create a plane mesh using the boundary points
plane_mesh_1 = trimesh.Trimesh(vertices=boundary, 
                            faces=[[0,1,2], [0,2,3], [0,1,3], [1,2,3]],
                            face_colors=[200, 200, 200, 100])

center = plane1[0].center
normal = plane1[0].normal
primary = plane1[0].primary
boundary = plane1[0].boundary

# Create a plane mesh using the boundary points
plane_mesh_2 = trimesh.Trimesh(vertices=boundary, 
                            faces=[[0,1,2], [0,2,3], [0,1,3], [1,2,3]],
                            face_colors=[200, 200, 200, 100])

# Add plane to scene
scene.add_geometry(plane_mesh_1)
scene.add_geometry(plane_mesh_2)

# Show the scene
scene.show()


In [10]:
vecx=[-0.5127623081207275, 0.5206868052482605, 0.6826127171516418]
vecy=[0.16300839185714722, 0.8396770358085632, -0.5180451273918152]
vecz=[0.8429134488105774, 0.15436242520809174, 0.5154310464859009]
# Convert vectors to numpy arrays for easier computation
vecx = np.array(vecx)
vecy = np.array(vecy)
vecz = np.array(vecz)

# Calculate dot products - should be close to 0 if perpendicular
dot_xy = np.dot(vecx, vecy)
dot_yz = np.dot(vecy, vecz)
dot_xz = np.dot(vecx, vecz)

print("Dot product of x and y vectors:", dot_xy)
print("Dot product of y and z vectors:", dot_yz) 
print("Dot product of x and z vectors:", dot_xz)

# Check if dot products are close to 0 (allowing for small numerical errors)
threshold = 1e-10
are_perpendicular = (abs(dot_xy) < threshold and 
                    abs(dot_yz) < threshold and 
                    abs(dot_xz) < threshold)

print("\nAre all vectors perpendicular to each other?", are_perpendicular)


Dot product of x and y vectors: 1.9476757984193682e-09
Dot product of y and z vectors: 7.265840373804622e-09
Dot product of x and z vectors: 1.9619915470059368e-08

Are all vectors perpendicular to each other? False
